# MAE experiments

This notebook just experiments with the impact of rounding and accuracy on the MAE.

To run it you may need to customise it - in my setup all the images are in the `unzip` directory and data files in the `data` directory. My local environmet looks like this
- unzip
  - planet-dec17
    - ... lots of `png` images
  - planet-dec18
    - ... lots of `png` images
  - planet-jun18
    - ... lots of `png` images
  - planet-jun18
    - ... lots of `png` images
  -sentinel
    - ... lots of `tif` images
- data
  - auxilary_data_unique.csv
  - extra_train.csv
  - test.csv
  - train-unique.csv

## License

MG Ferreira<br/>
&copy; Ferra Solutions (Pty) Ltd https://www.ferrasolutions.com</br>
Note that this is *copyrighted* material.

You are welcome to use it to compete, but you can not publish this notebook elsewhere as if you created it, or use it in e.g. a lecture or as part of a paper or in some other setting without written permission from me.

## Disclaimer

This does not imply anything and is just a toy example to play with at your own risk.

In [ ]:
import skimage.io
import pandas     as pd
import numpy      as np

# Data paths - customise for your environment
data_path = 'data'
img_path  = 'unzip'

In [ ]:
# Some utilities, mostly taken from the starter or derived directly from info in the starter
CONST_X    = 10.986328125 / 2
CONST_Y    = 10.985731758 / 2

# Load the training and auxilliary data
def load_data ():

    train = pd.read_csv ( f'{ data_path }/train-unique.csv' )
    aux   = pd.read_csv ( f'{ data_path }/auxilary_data-unique.csv' )
    extra = pd.read_csv ( f'{ data_path }/extra_train.csv' )

    return pd.concat ( [ train, aux, extra ] )

# Get image center in image pixels
def img_center_pixels ( img ):

    return img.shape [ 1 ] // 2, img.shape [ 0 ] // 2

# Given an image and target coordinates, return the target location in image pixels
def img_target_pixels ( img, tgtx, tgty ):

    ctr = img_center_pixels ( img )

    x1 = ctr [ 0 ] - np.round ( tgtx / CONST_X * img.shape [ 1 ] )
    y1 = ctr [ 1 ] + np.round ( tgty / CONST_Y * img.shape [ 0 ] )

    return int ( x1 ), int ( y1 )

# Given an image, the image center and some location in pixels, return the target coordinates
def img_pixels_target ( img, pixx, pixy ):

    ctr = img_center_pixels ( img )

    x   = CONST_X * float ( ctr [ 0 ] - pixx ) / float ( img.shape [ 1 ] )
    y   = CONST_Y * float ( pixy - ctr [ 1 ] ) / float ( img.shape [ 0 ] )

    return x, y

# Supplied - load RGB image
def load_RGB_images ( ID ):

    # e.g id_0b242e06 -> 0b242e06
    name      = ID.split('_')[1]

    img_jun17 = skimage.io.imread ( f'{img_path}/planet-jun17/{name}.png' )
    img_dec17 = skimage.io.imread ( f'{img_path}/planet-dec17/{name}.png' )
    img_jun18 = skimage.io.imread ( f'{img_path}/planet-jun18/{name}.png' )
    img_dec18 = skimage.io.imread ( f'{img_path}/planet-dec18/{name}.png' )

    return img_jun17, img_dec17, img_jun18, img_dec18

# Load the RGB mages and return them as a stack
def load_rgb_stack ( ID ):

    rgbs = load_RGB_images ( ID )
    return np.concatenate ( [ rgbs [ 0 ], rgbs [ 1 ], rgbs [ 2 ], rgbs [ 3 ] ], axis = 2 )

In [ ]:
# Iterate through the data and report the perfectly accurate plot center
# accurate to a pixel and then accurate to half a pixel

data     = load_data ()
mae      = 0.0
mae_half = 0.0
n        = 0

for irow, row in data.iterrows ():

    img      = load_rgb_stack ( row.ID )
    px, py   = img_target_pixels ( img, row.x, row.y )
    x, y     = img_pixels_target ( img, px, py )
    xu, yu   = img_pixels_target ( img, px + 0.5, py + 0.5 )
    xl, yl   = img_pixels_target ( img, px - 0.5, py - 0.5 )
    mae      = mae + abs ( x - row.x ) + abs ( y - row.y )
    mae_half = mae_half + min ( abs ( xu - row.x ), abs ( x - row.x ), abs ( xl - row.x ) ) \
                        + min ( abs ( yu - row.y ), abs ( y - row.y ), abs ( yl - row.y ) )
    n        = n + 2

mae      = mae      / n
mae_half = mae_half / n

print ( f"MAE accurate to pixel      { mae }" )
print ( f"MAE accurate to half pixel { mae_half }" )